<a href="https://colab.research.google.com/github/Matendy12/Project-4/blob/main/IMDB_Movies_Kmeans_Model.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [10]:
!pip install hvplot


In [18]:
!pip install pandas scikit-learn

In [19]:
# IMPORTANT: RUN THIS CELL IN ORDER TO IMPORT YOUR KAGGLE DATA SOURCES
# TO THE CORRECT LOCATION (/kaggle/input) IN YOUR NOTEBOOK,
# THEN FEEL FREE TO DELETE THIS CELL.
# NOTE: THIS NOTEBOOK ENVIRONMENT DIFFERS FROM KAGGLE'S PYTHON
# ENVIRONMENT SO THERE MAY BE MISSING LIBRARIES USED BY YOUR
# NOTEBOOK.

import os
import sys
from tempfile import NamedTemporaryFile
from urllib.request import urlopen
from urllib.parse import unquote, urlparse
from urllib.error import HTTPError
from zipfile import ZipFile
import tarfile
import shutil

CHUNK_SIZE = 40960
DATA_SOURCE_MAPPING = 'imdb-dataset-of-top-1000-movies-and-tv-shows:https%3A%2F%2Fstorage.googleapis.com%2Fkaggle-data-sets%2F1131493%2F1898721%2Fbundle%2Farchive.zip%3FX-Goog-Algorithm%3DGOOG4-RSA-SHA256%26X-Goog-Credential%3Dgcp-kaggle-com%2540kaggle-161607.iam.gserviceaccount.com%252F20240417%252Fauto%252Fstorage%252Fgoog4_request%26X-Goog-Date%3D20240417T095449Z%26X-Goog-Expires%3D259200%26X-Goog-SignedHeaders%3Dhost%26X-Goog-Signature%3D7dd260818c2a780b774d7c9381839b159079016d2e825bb2e9cb0bd7c42c9f5bab456445dfadbdf5896a2b8b4473456dd350f6b05398b6ae194d0594759c633bf40de14ed3e03a98c1c4f5611ef5f10bcd87dff67b5494f63b41e1152178ef6820c9318482f1cad33ec040c081b0c5338dbb07a76a30fa80fecfc106af490f1316fe679220b229993b2e13e8fb965e72fbeed21cb65ad6a0d78912f921981cf71ea45575175bc4bcde0b1fb4829d39acc05e03677e2725d2532d6b8d4a279459b4436606c8f231ed0c7b9b8f728c23be72a8c69d63216db226fd7a5bfe9646a7eaa40416b6fa32bf8f74d3afe127c1ab82e112f0e3c08200f7fefbd12c0d3ae8,data-science-salaries-2023:https%3A%2F%2Fstorage.googleapis.com%2Fkaggle-data-sets%2F3125926%2F5392837%2Fbundle%2Farchive.zip%3FX-Goog-Algorithm%3DGOOG4-RSA-SHA256%26X-Goog-Credential%3Dgcp-kaggle-com%2540kaggle-161607.iam.gserviceaccount.com%252F20240417%252Fauto%252Fstorage%252Fgoog4_request%26X-Goog-Date%3D20240417T095449Z%26X-Goog-Expires%3D259200%26X-Goog-SignedHeaders%3Dhost%26X-Goog-Signature%3D3b7368cbe133495b14200387b7e18fd2e237050cc994682bfbbbc693aae78a5a9471695a91e51fc42fbf559d0a03659e600aeaa4e190ffca96465a89014a66c07132f7d0a11604cee71e34da19ed8ed604bf8b83fe2d35882680b9faa498699c171ca25dc9fcbb7102d314d46e01b4398a965800de5cff857345b3aa95161da00fd21fed01d86904bb17b6dcfd3665350a4646b4536912f5eb961cd1ad4a1b5bde4ac8479066e5bd1846d2c41e9c72fc4f357191d265a8245e57a8c5d7607f6ee7c37d09c2375a31866b7842c77549b85b8e7d6fed00154ed0879016b512276599e4cae5a3091403332b6dbbf185893ec9fce061d1314f84af9d370818715d95'

KAGGLE_INPUT_PATH='/kaggle/input'
KAGGLE_WORKING_PATH='/kaggle/working'
KAGGLE_SYMLINK='kaggle'

!umount /kaggle/input/ 2> /dev/null
shutil.rmtree('/kaggle/input', ignore_errors=True)
os.makedirs(KAGGLE_INPUT_PATH, 0o777, exist_ok=True)
os.makedirs(KAGGLE_WORKING_PATH, 0o777, exist_ok=True)

try:
  os.symlink(KAGGLE_INPUT_PATH, os.path.join("..", 'input'), target_is_directory=True)
except FileExistsError:
  pass
try:
  os.symlink(KAGGLE_WORKING_PATH, os.path.join("..", 'working'), target_is_directory=True)
except FileExistsError:
  pass

for data_source_mapping in DATA_SOURCE_MAPPING.split(','):
    directory, download_url_encoded = data_source_mapping.split(':')
    download_url = unquote(download_url_encoded)
    filename = urlparse(download_url).path
    destination_path = os.path.join(KAGGLE_INPUT_PATH, directory)
    try:
        with urlopen(download_url) as fileres, NamedTemporaryFile() as tfile:
            total_length = fileres.headers['content-length']
            print(f'Downloading {directory}, {total_length} bytes compressed')
            dl = 0
            data = fileres.read(CHUNK_SIZE)
            while len(data) > 0:
                dl += len(data)
                tfile.write(data)
                done = int(50 * dl / int(total_length))
                sys.stdout.write(f"\r[{'=' * done}{' ' * (50-done)}] {dl} bytes downloaded")
                sys.stdout.flush()
                data = fileres.read(CHUNK_SIZE)
            if filename.endswith('.zip'):
              with ZipFile(tfile) as zfile:
                zfile.extractall(destination_path)
            else:
              with tarfile.open(tfile.name) as tarfile:
                tarfile.extractall(destination_path)
            print(f'\nDownloaded and uncompressed: {directory}')
    except HTTPError as e:
        print(f'Failed to load (likely expired) {download_url} to path {destination_path}')
        continue
    except OSError as e:
        print(f'Failed to load {download_url} to path {destination_path}')
        continue

print('Data source import complete.')

[==================================================] 179262 bytes downloaded
Downloaded and uncompressed: imdb-dataset-of-top-1000-movies-and-tv-shows
[==================================================] 26034 bytes downloaded
Downloaded and uncompressed: data-science-salaries-2023
Data source import complete.


In [20]:
# Import required libraries and dependencies
import pandas as pd
import hvplot.pandas
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
#from itables import init_notebook_mode
#init_notebook_mode(all_interactive = True)
import warnings
warnings.filterwarnings('ignore')

In [21]:
movies_df= pd.read_csv("/kaggle/input/imdb-dataset-of-top-1000-movies-and-tv-shows/imdb_top_1000.csv"
 index_col="coin_id")
movies_df.head()

# Display sample data
movies_df.head(10)

Poster_Link  \
0  https://m.media-amazon.com/images/M/MV5BMDFkYT...   
1  https://m.media-amazon.com/images/M/MV5BM2MyNj...   
2  https://m.media-amazon.com/images/M/MV5BMTMxNT...   
3  https://m.media-amazon.com/images/M/MV5BMWMwMG...   
4  https://m.media-amazon.com/images/M/MV5BMWU4N2...   
5  https://m.media-amazon.com/images/M/MV5BNzA5ZD...   
6  https://m.media-amazon.com/images/M/MV5BNGNhMD...   
7  https://m.media-amazon.com/images/M/MV5BNDE4OT...   
8  https://m.media-amazon.com/images/M/MV5BMjAxMz...   
9  https://m.media-amazon.com/images/M/MV5BMmEzNT...   

                                    Series_Title Released_Year Certificate  \
0                       The Shawshank Redemption          1994           A   
1                                  The Godfather          1972           A   
2                                The Dark Knight          2008          UA   
3                         The Godfather: Part II          1974           A   
4                                   12 Angry Men          1957           U   
5  The Lord of the Rings: The Return of the King          2003           U   
6                                   Pulp Fiction          1994           A   
7                               Schindler's List          1993           A   
8                                      Inception          2010          UA   
9                                     Fight Club          1999           A   

   Runtime                      Genre  IMDB_Rating  \
0  142 min                      Drama          9.3   
1  175 min               Crime, Drama          9.2   
2  152 min       Action, Crime, Drama          9.0   
3  202 min               Crime, Drama          9.0   
4   96 min               Crime, Drama          9.0   
5  201 min   Action, Adventure, Drama          8.9   
6  154 min               Crime, Drama          8.9   
7  195 min  Biography, Drama, History          8.9   
8  148 min  Action, Adventure, Sci-Fi          8.8   
9  139 min                      Drama          8.8   

                                            Overview  Meta_score  \
0  Two imprisoned men bond over a number of years...        80.0   
1  An organized crime dynasty's aging patriarch t...       100.0   
2  When the menace known as the Joker wreaks havo...        84.0   
3  The early life and career of Vito Corleone in ...        90.0   
4  A jury holdout attempts to prevent a miscarria...        96.0   
5  Gandalf and Aragorn lead the World of Men agai...        94.0   
6  The lives of two mob hitmen, a boxer, a gangst...        94.0   
7  In German-occupied Poland during World War II,...        94.0   
8  A thief who steals corporate secrets through t...        74.0   
9  An insomniac office worker and a devil-may-car...        66.0   

               Director              Star1                 Star2  \
0        Frank Darabont        Tim Robbins        Morgan Freeman   
1  Francis Ford Coppola      Marlon Brando             Al Pacino   
2     Christopher Nolan     Christian Bale          Heath Ledger   
3  Francis Ford Coppola          Al Pacino        Robert De Niro   
4          Sidney Lumet        Henry Fonda           Lee J. Cobb   
5         Peter Jackson        Elijah Wood       Viggo Mortensen   
6     Quentin Tarantino      John Travolta           Uma Thurman   
7      Steven Spielberg        Liam Neeson         Ralph Fiennes   
8     Christopher Nolan  Leonardo DiCaprio  Joseph Gordon-Levitt   
9         David Fincher          Brad Pitt         Edward Norton   

               Star3             Star4  No_of_Votes        Gross  
0         Bob Gunton    William Sadler      2343110   28,341,469  
1         James Caan      Diane Keaton      1620367  134,966,411  
2      Aaron Eckhart     Michael Caine      2303232  534,858,444  
3      Robert Duvall      Diane Keaton      1129952   57,300,000  
4      Martin Balsam      John Fiedler       689845    4,360,000  
5       Ian McKellen     Orlando Bloom      1642758  377,845,905  
6  

In [22]:
# Generate summary statistics
movies_df.describe()

IMDB_Rating  Meta_score   No_of_Votes
count  1000.000000  843.000000  1.000000e+03
mean      7.949300   77.971530  2.736929e+05
std       0.275491   12.376099  3.273727e+05
min       7.600000   28.000000  2.508800e+04
25%       7.700000   70.000000  5.552625e+04
50%       7.900000   79.000000  1.385485e+05
75%       8.100000   87.000000  3.741612e+05
max       9.300000  100.000000  2.343110e+06

from matplotlib import pyplot as plt
_df_62['IMDB_Rating'].plot(kind='hist', bins=20, title='IMDB_Rating')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_63['Meta_score'].plot(kind='hist', bins=20, title='Meta_score')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_64['No_of_Votes'].plot(kind='hist', bins=20, title='No_of_Votes')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_65.plot(kind='scatter', x='IMDB_Rating', y='Meta_score', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_66.plot(kind='scatter', x='Meta_score', y='No_of_Votes', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_67['IMDB_Rating'].plot(kind='line', figsize=(8, 4), title='IMDB_Rating')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_68['Meta_score'].plot(kind='line', figsize=(8, 4), title='Meta_score')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_69['No_of_Votes'].plot(kind='line', figsize=(8, 4), title='No_of_Votes')
plt.gca().spines[['top', 'right']].set_visible(False)

In [23]:
# Plot your data to see what's in your DataFrame
movies_df.hvplot.line(
    width=800,
    height=400,
    rot=90
)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

---

### Prepare the Data

In [25]:
movies_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 16 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Poster_Link    1000 non-null   object 
 1   Series_Title   1000 non-null   object 
 2   Released_Year  1000 non-null   object 
 3   Certificate    899 non-null    object 
 4   Runtime        1000 non-null   object 
 5   Genre          1000 non-null   object 
 6   IMDB_Rating    1000 non-null   float64
 7   Overview       1000 non-null   object 
 8   Meta_score     843 non-null    float64
 9   Director       1000 non-null   object 
 10  Star1          1000 non-null   object 
 11  Star2          1000 non-null   object 
 12  Star3          1000 non-null   object 
 13  Star4          1000 non-null   object 
 14  No_of_Votes    1000 non-null   int64  
 15  Gross          831 non-null    object 
dtypes: float64(2), int64(1), object(13)
memory usage: 125.1+ KB


In [26]:
non_numerical_columns = movies_df.select_dtypes(include=["object"]).columns.tolist()

In [27]:
movies_df_numerical = movies_df.drop(non_numerical_columns, axis=1)

In [28]:
scaler = StandardScaler()
movies_df_scaled = scaler.fit_transform(movies_df_numerical)

In [30]:
# Use the `StandardScaler()` module from scikit-learn to normalize the data from the CSV file

movies_df_scaled[0:5]

array([[4.90533208, 0.16399949, 6.32445085],
       [4.54216246, 1.78097689, 4.11563919],
       [3.81582321, 0.48739497, 6.20257766],
       [3.81582321, 0.97248819, 2.61685696],
       [3.81582321, 1.45758141, 1.27182357]])

In [33]:
# Create a DataFrame with the scaled data
movies_df_scaled =  pd.DataFrame(movies_df_scaled, columns=(["Poster_Link",
                                                             "Series_Title",
                                                             "Released_Year"
                                                              ]))

# Copy the crypto names from the original data
movies_df_scaled['coin_id'] = movies_df.index

# Set the coinid column as index
movies_df_scaled = movies_df_scaled.set_index('coin_id')

# Display sample data
movies_df_scaled.head()

Poster_Link  Series_Title  Released_Year
coin_id                                          
0           4.905332      0.163999       6.324451
1           4.542162      1.780977       4.115639
2           3.815823      0.487395       6.202578
3           3.815823      0.972488       2.616857
4           3.815823      1.457581       1.271824

from matplotlib import pyplot as plt
_df_54['Poster_Link'].plot(kind='hist', bins=20, title='Poster_Link')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_55['Series_Title'].plot(kind='hist', bins=20, title='Series_Title')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_56['Released_Year'].plot(kind='hist', bins=20, title='Released_Year')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_57.plot(kind='scatter', x='Poster_Link', y='Series_Title', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_58.plot(kind='scatter', x='Series_Title', y='Released_Year', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_59['Poster_Link'].plot(kind='line', figsize=(8, 4), title='Poster_Link')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_60['Series_Title'].plot(kind='line', figsize=(8, 4), title='Series_Title')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_61['Released_Year'].plot(kind='line', figsize=(8, 4), title='Released_Year')
plt.gca().spines[['top', 'right']].set_visible(False)

---

### Find the Best Value for k Using the Original Data.

In [34]:
# Create a list with the number of k-values from 1 to 11
inertia = []
k = list(range(1, 11))

In [36]:
movies_df_scaled.isnull().sum()

Poster_Link        0
Series_Title     157
Released_Year      0
dtype: int64

In [38]:
movies_df_scaled.dropna(inplace=True)

In [39]:
# Create an empty list to store the inertia values
inertia = []

# Create a for loop to compute the inertia with each possible value of k
# Inside the loop:
# 1. Create a KMeans model using the loop counter for the n_clusters
# 2. Fit the model to the data using `df_market_data_scaled`
# 3. Append the model.inertia_ to the inertia list
for i in k:
    k_model = KMeans(n_clusters=i, random_state=0)
    k_model.fit(movies_df_scaled)
    inertia.append(k_model.inertia_)


In [40]:
# Create a dictionary with the data to plot the Elbow curve
elbow_data = {"k": k, "inertia": inertia}
df_elbow = pd.DataFrame(elbow_data)

# Create a DataFrame with the data to plot the Elbow curve
df_elbow.head()

k      inertia
0  1  2655.784062
1  2  1708.627724
2  3  1213.834786
3  4  1009.805290
4  5   846.739914

from matplotlib import pyplot as plt
_df_47['k'].plot(kind='hist', bins=20, title='k')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_48['inertia'].plot(kind='hist', bins=20, title='inertia')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_49.plot(kind='scatter', x='k', y='inertia', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['k']
  ys = series['inertia']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_50.sort_values('k', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('k')
_ = plt.ylabel('inertia')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['k']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'k'}, axis=1)
              .sort_values('k', ascending=True))
  xs = counted['k']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_51.sort_values('k', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('k')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_52['k'].plot(kind='line', figsize=(8, 4), title='k')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_53['inertia'].plot(kind='line', figsize=(8, 4), title='inertia')
plt.gca().spines[['top', 'right']].set_visible(False)

In [41]:
# Plot a line chart with all the inertia values computed with
# the different values of k to visually identify the optimal value for k.
df_elbow.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

#### Answer the following question:

**Question:** What is the best value for `k`?

**Answer:** It looks like the best value for k is 4 according to the elbow curve above.

---

### Cluster Cryptocurrencies with K-means Using the Original Data

In [42]:
# Initialize the K-Means model using the best value for k
model = KMeans(n_clusters=4, random_state=0)

In [43]:
# Fit the K-Means model using the scaled data
model.fit(movies_df_scaled)

KMeans(n_clusters=4, random_state=0)

In [44]:
# Predict the clusters to group the cryptocurrencies using the scaled data
crypto_clusters = model.predict(movies_df_scaled)

# Print the resulting array of cluster values.
print(crypto_clusters)

[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 3 3 0 0 3 0 0 0 0 0 0 3 3 3 0 3 0 0 0
 3 0 0 0 0 0 0 3 3 0 3 3 3 3 3 3 3 3 3 0 3 0 0 3 0 3 3 0 3 3 0 3 3 3 3 3 3
 3 3 3 0 3 3 3 3 0 3 3 3 0 3 3 3 3 3 0 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 3 1 2
 2 3 3 0 3 0 1 3 3 3 0 0 3 3 3 3 3 3 3 3 3 3 3 2 3 3 3 3 1 3 2 3 2 3 2 2 2
 2 2 2 2 2 3 3 2 2 2 3 3 1 3 3 3 3 3 3 2 3 3 3 3 1 3 3 3 3 3 1 2 2 3 3 3 2
 3 2 3 1 3 2 3 2 3 3 3 2 2 3 2 3 3 3 2 2 1 1 2 3 3 3 3 3 2 2 3 2 2 2 2 2 2
 2 2 2 2 2 2 2 2 2 2 2 2 2 2 1 3 1 3 3 2 1 1 2 1 3 3 3 3 1 3 1 1 3 1 3 2 1
 1 3 3 1 0 2 3 1 1 3 1 3 2 3 3 3 2 2 2 1 1 2 3 1 3 1 3 2 1 2 2 2 2 2 2 3 2
 2 3 1 1 3 1 3 1 2 1 3 2 2 2 3 2 2 2 2 3 2 2 1 3 2 1 2 1 2 2 2 2 1 1 1 2 2
 2 2 2 2 2 2 2 2 2 2 2 1 2 2 2 2 2 2 2 2 3 2 2 2 2 2 2 1 2 3 3 1 3 3 2 3 2
 2 1 2 2 2 1 2 3 2 2 2 3 1 2 1 3 2 2 1 3 3 2 2 3 2 2 2 1 1 2 3 2 2 3 2 2 2
 1 2 1 1 2 2 2 2 2 2 2 1 2 1 1 2 2 2 1 2 2 2 2 2 2 2 2 1 2 2 2 2 2 2 2 2 1
 2 2 2 1 2 2 2 1 1 3 1 2 1 2 2 2 2 1 1 2 2 1 2 1 2 1 1 2 1 2 1 1 2 1 2 2 2
 1 1 2 1 2 2 3 1 3 1 1 2 

In [45]:
# Create a copy of the DataFrame
movies_df_scaled_predictions = movies_df_scaled.copy()

In [46]:
# Add a new column to the DataFrame with the predicted clusters
movies_df_scaled_predictions["CryptoCluster"] = crypto_clusters

# Display sample data
movies_df_scaled_predictions.head()

Poster_Link  Series_Title  Released_Year  CryptoCluster
coin_id                                                         
0           4.905332      0.163999       6.324451              0
1           4.542162      1.780977       4.115639              0
2           3.815823      0.487395       6.202578              0
3           3.815823      0.972488       2.616857              0
4           3.815823      1.457581       1.271824              0

from matplotlib import pyplot as plt
_df_35['Poster_Link'].plot(kind='hist', bins=20, title='Poster_Link')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_36['Series_Title'].plot(kind='hist', bins=20, title='Series_Title')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_37['Released_Year'].plot(kind='hist', bins=20, title='Released_Year')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_38.plot(kind='scatter', x='Poster_Link', y='Series_Title', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['CryptoCluster']
  ys = series['Released_Year']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_42.sort_values('CryptoCluster', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('CryptoCluster')
_ = plt.ylabel('Released_Year')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['CryptoCluster']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'CryptoCluster'}, axis=1)
              .sort_values('CryptoCluster', ascending=True))
  xs = counted['CryptoCluster']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_43.sort_values('CryptoCluster', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('CryptoCluster')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_44['Poster_Link'].plot(kind='line', figsize=(8, 4), title='Poster_Link')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_45['Series_Title'].plot(kind='line', figsize=(8, 4), title='Series_Title')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_46['Released_Year'].plot(kind='line', figsize=(8, 4), title='Released_Year')
plt.gca().spines[['top', 'right']].set_visible(False)

In [47]:
movies_df_scaled.head()

Poster_Link  Series_Title  Released_Year
coin_id                                          
0           4.905332      0.163999       6.324451
1           4.542162      1.780977       4.115639
2           3.815823      0.487395       6.202578
3           3.815823      0.972488       2.616857
4           3.815823      1.457581       1.271824

from matplotlib import pyplot as plt
_df_27['Poster_Link'].plot(kind='hist', bins=20, title='Poster_Link')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_28['Series_Title'].plot(kind='hist', bins=20, title='Series_Title')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_29['Released_Year'].plot(kind='hist', bins=20, title='Released_Year')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_30.plot(kind='scatter', x='Poster_Link', y='Series_Title', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_31.plot(kind='scatter', x='Series_Title', y='Released_Year', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_32['Poster_Link'].plot(kind='line', figsize=(8, 4), title='Poster_Link')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_33['Series_Title'].plot(kind='line', figsize=(8, 4), title='Series_Title')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_34['Released_Year'].plot(kind='line', figsize=(8, 4), title='Released_Year')
plt.gca().spines[['top', 'right']].set_visible(False)

In [48]:
movies_df_scaled.dtypes

Poster_Link      float64
Series_Title     float64
Released_Year    float64
dtype: object

In [49]:
# Create a scatter plot using hvPlot by setting
# `x="price_change_percentage_24h"` and `y="price_change_percentage_7d"`.
# Color the graph points with the labels found using K-Means and
# add the crypto name in the `hover_cols` parameter to identify
# the cryptocurrency represented by each data point.
scatter_plot = movies_df_scaled_predictions.hvplot.scatter(
    x= "Poster_Link",
    y= "Series_Title",
    by= "Released_Year",
    hover_cols=["coin_id"],
    title = "Scatter Plot by Crypto Currency Using Scaled Data"
)
scatter_plot

:NdOverlay   [Released_Year]
   :Scatter   [Poster_Link]   (Series_Title,coin_id)

---

### Optimize Clusters with Principal Component Analysis.

In [50]:
# Create a PCA model instance and set `n_components=3`.
pca=PCA(n_components=3)

In [51]:
# Use the PCA model with `fit_transform` to reduce to
# three principal components.
clusters_pca = pca.fit_transform(movies_df_scaled)
# View the first five rows of the DataFrame.
clusters_pca[:5]

array([[ 7.6766873 ,  2.02043211, -0.44065469],
       [ 6.34192904, -0.32197192,  0.15677376],
       [ 6.90538896,  1.74913803, -1.23938222],
       [ 4.63528549, -0.14024114,  0.85097299],
       [ 3.85730145, -1.1255816 ,  1.53527941]])

In [52]:
# Retrieve the explained variance to determine how much information
# can be attributed to each principal component.
pca.explained_variance_ratio_

array([0.55580488, 0.326576  , 0.11761912])

In [54]:
# Create the PCA DataFrame
clusters_pca_df = pd.DataFrame(
    clusters_pca,
    columns=["PCA1", "PCA2", "PCA3"]
)
# Copy the crypto names from the original data
clusters_pca_df['coin_id'] = list(movies_df_scaled_predictions.index)
clusters_pca_df

# Set the coinid column as index
clusters_pca_df = clusters_pca_df.set_index('coin_id')

# Review the PCA DataFrame
clusters_pca_df.head()

PCA1      PCA2      PCA3
coin_id                              
0        7.676687  2.020432 -0.440655
1        6.341929 -0.321972  0.156774
2        6.905389  1.749138 -1.239382
3        4.635285 -0.140241  0.850973
4        3.857301 -1.125582  1.535279

from matplotlib import pyplot as plt
_df_19['PCA1'].plot(kind='hist', bins=20, title='PCA1')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_20['PCA2'].plot(kind='hist', bins=20, title='PCA2')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_21['PCA3'].plot(kind='hist', bins=20, title='PCA3')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_22.plot(kind='scatter', x='PCA1', y='PCA2', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_23.plot(kind='scatter', x='PCA2', y='PCA3', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_24['PCA1'].plot(kind='line', figsize=(8, 4), title='PCA1')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_25['PCA2'].plot(kind='line', figsize=(8, 4), title='PCA2')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_26['PCA3'].plot(kind='line', figsize=(8, 4), title='PCA3')
plt.gca().spines[['top', 'right']].set_visible(False)

#### Answer the following question:

**Question:** What is the total explained variance of the three principal components?

**Answer:**

In [55]:
# Create a new DataFrame with the PCA data.
model = KMeans(n_clusters=3, random_state=0)

# Creating a DataFrame with the PCA data
model.fit(clusters_pca_df)

# Copy the crypto names from the original data
k_3 = model.predict(clusters_pca_df)

# Set the coinid column as index
clusters_pca_predictions = clusters_pca_df.copy()

# Display sample data
clusters_pca_predictions["customer_segments"] = k_3

In [56]:
# Plot the clusters
clusters_pca_predictions.hvplot.scatter(
    x="PCA1",
    y="PCA3",
    by="customer_segments"
)

:NdOverlay   [customer_segments]
   :Scatter   [PCA1]   (PCA3)

---

### Find the Best Value for k Using the PCA Data

In [57]:
# Create a list with the number of k-values from 1 to 11
inertia = []
k = list(range(1, 11))

In [58]:
# Create an empty list to store the inertia values
inertia = []

# Create a for loop to compute the inertia with each possible value of k
# Inside the loop:
# 1. Create a KMeans model using the loop counter for the n_clusters
# 2. Fit the model to the data using `df_market_data_pca`
# 3. Append the model.inertia_ to the inertia list
for i in k:
    k_model = KMeans(n_clusters=i, random_state=0)
    k_model.fit(clusters_pca_df)
    inertia.append(k_model.inertia_)

In [59]:
# Create a dictionary with the data to plot the Elbow curve
elbow_data_2 = {"k": k, "inertia": inertia}
# Create a DataFrame with the data to plot the Elbow curve
df_elbow_2 = pd.DataFrame(elbow_data_2)
df_elbow_2.head()

k      inertia
0  1  2655.784062
1  2  1708.627724
2  3  1213.834786
3  4  1009.805290
4  5   846.739914

from matplotlib import pyplot as plt
_df_12['k'].plot(kind='hist', bins=20, title='k')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_13['inertia'].plot(kind='hist', bins=20, title='inertia')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_14.plot(kind='scatter', x='k', y='inertia', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['k']
  ys = series['inertia']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_15.sort_values('k', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('k')
_ = plt.ylabel('inertia')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['k']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'k'}, axis=1)
              .sort_values('k', ascending=True))
  xs = counted['k']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_16.sort_values('k', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('k')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_17['k'].plot(kind='line', figsize=(8, 4), title='k')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_18['inertia'].plot(kind='line', figsize=(8, 4), title='inertia')
plt.gca().spines[['top', 'right']].set_visible(False)

In [60]:
# Plot a line chart with all the inertia values computed with
# the different values of k to visually identify the optimal value for k.
df_elbow_2.hvplot.line(
    x="k",
    y="inertia",
    title="Elbow Curve",
    xticks=k
)

:Curve   [k]   (inertia)

#### Answer the following questions:

* **Question:** What is the best value for `k` when using the PCA data?

  * **Answer:**The best value for k is 4.


* **Question:** Does it differ from the best k value found using the original data?

  * **Answer:**  It is the same as the original data.

### Cluster Cryptocurrencies with K-means Using the PCA Data

In [61]:
# Initialize the K-Means model using the best value for k
model = KMeans(n_clusters=4, random_state=0)

In [62]:
# Fit the K-Means model using the PCA data
model.fit(clusters_pca_predictions)

KMeans(n_clusters=4, random_state=0)

In [63]:
# Predict the clusters to group the cryptocurrencies using the PCA data
k_3 = model.predict(clusters_pca_predictions)
# Print the resulting array of cluster values.
print(clusters_pca_predictions)

             PCA1      PCA2      PCA3  customer_segments
coin_id                                                 
0        7.676687  2.020432 -0.440655                  1
1        6.341929 -0.321972  0.156774                  1
2        6.905389  1.749138 -1.239382                  1
3        4.635285 -0.140241  0.850973                  1
4        3.857301 -1.125582  1.535279                  1
...           ...       ...       ...                ...
995     -1.186870  0.045331 -0.516182                  0
996     -1.299530 -0.708232 -0.475088                  2
997     -1.260989 -0.770543 -0.519540                  2
998     -1.432707 -0.274941 -0.300793                  0
999     -1.086798 -1.350311 -0.748751                  2

[843 rows x 4 columns]


In [64]:
# Create a copy of the DataFrame with the PCA data
clusters_pca_predictions_df = clusters_pca_df.copy()

# Add a new column to the DataFrame with the predicted clusters
clusters_pca_predictions_df["customer_segments"] = k_3

# Display sample data
clusters_pca_predictions_df.head()

PCA1      PCA2      PCA3  customer_segments
coin_id                                                 
0        7.676687  2.020432 -0.440655                  2
1        6.341929 -0.321972  0.156774                  2
2        6.905389  1.749138 -1.239382                  2
3        4.635285 -0.140241  0.850973                  2
4        3.857301 -1.125582  1.535279                  2

from matplotlib import pyplot as plt
_df_0['PCA1'].plot(kind='hist', bins=20, title='PCA1')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_1['PCA2'].plot(kind='hist', bins=20, title='PCA2')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_2['PCA3'].plot(kind='hist', bins=20, title='PCA3')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_3.plot(kind='scatter', x='PCA1', y='PCA2', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['customer_segments']
  ys = series['PCA3']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_7.sort_values('customer_segments', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('customer_segments')
_ = plt.ylabel('PCA3')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['customer_segments']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'customer_segments'}, axis=1)
              .sort_values('customer_segments', ascending=True))
  xs = counted['customer_segments']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_8.sort_values('customer_segments', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('customer_segments')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_9['PCA1'].plot(kind='line', figsize=(8, 4), title='PCA1')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_10['PCA2'].plot(kind='line', figsize=(8, 4), title='PCA2')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_11['PCA3'].plot(kind='line', figsize=(8, 4), title='PCA3')
plt.gca().spines[['top', 'right']].set_visible(False)

In [65]:
# Create a scatter plot using hvPlot by setting
# `x="PC1"` and `y="PC2"`.
# Color the graph points with the labels found using K-Means and
# add the crypto name in the `hover_cols` parameter to identify
# the cryptocurrency represented by each data point.
clusters_pca_predictions_df.hvplot.scatter(
    x="PCA1",
    y="PCA2",
    by="customer_segments",
    hover_cols="coin_id"
)

:NdOverlay   [customer_segments]
   :Scatter   [PCA1]   (PCA2,coin_id)

### Visualize and Compare the Results

In this section, you will visually analyze the cluster analysis results by contrasting the outcome with and without using the optimization techniques.

In [66]:
# Composite plot to contrast the Elbow curves
e_1 = df_elbow.hvplot.line(x="k", y="inertia", title= "Elbow Curve 1", xticks=k)
e_2 = df_elbow_2.hvplot.line(x="k", y="inertia", title="Elbow Curve 2", xticks=k)
e_1 + e_2

:Layout
   .Curve.I  :Curve   [k]   (inertia)
   .Curve.II :Curve   [k]   (inertia)

In [68]:
# Composite plot to contrast the clusters
c1 = movies_df_scaled_predictions.hvplot.scatter( x='Poster_Link', y='Series_Title', by='Released_Year', hover_cols = 'coin_id')
c2 = clusters_pca_predictions_df.hvplot.scatter(x="PCA1", y="PCA2", by = 'customer_segments', hover_cols='coin_id')

In [69]:
c1 + c2

:Layout
   .NdOverlay.I  :NdOverlay   [Released_Year]
      :Scatter   [Poster_Link]   (Series_Title,coin_id)
   .NdOverlay.II :NdOverlay   [customer_segments]
      :Scatter   [PCA1]   (PCA2,coin_id)

#### Answer the following question:

  * **Question:** After visually analyzing the cluster analysis results, what is the impact of using fewer features to cluster the data using K-Means?

  * **Answer:** The clusters become more distinct and easier to see visually. PCA removes less informative features from the data, as it retains the most significance variance in the original dataset. The second scatterplot above for PCA, shows four distinct clusters, with 'ethland' in orange and 'celsius-degree-token' in yellow. There two cryptocurrencies incidently showed significantly higher percentage price change at 200d and 1 year, compared to all the other cryptocurrencies. Splitting these two out into their own clusters makes sense.